# Genomic Data for Variant Pathogenicity
This notebook reads the vcf file containing ClinVar data and outputs a vcf file that contains the right information to run ANNOVAR and, eventually reach the table templated format provide in FH-EARLY for the genomic data.

### To download the ClinVar data:
Go to https://ftp.ncbi.nlm.nih.gov/pub/clinvar/vcf_GRCh38/ (Our version is clinvar_20260208.vcf.gz and also clinvar_20260208.vcf.gz.tbi)

In [65]:
# import packages
import pandas as pd
pd.set_option('display.max_columns', None)
from cyvcf2 import VCF # https://github.com/brentp/cyvcf2/tree/main

### Variable choices
1. Genome Interval (ClinVar): consulted https://www-ncbi-nlm-nih-gov.tudelft.idm.oclc.org/clinvar/?term=LDLR%5Bgene%5D to select the range between the first and the last LDLR variant in chromosome 19.
2. Variable description for VCF file: https://ftp.ncbi.nlm.nih.gov/pub/clinvar/README_VCF.txt
3. Variables ANNOVAR (following MetaRNN paper - additional file):
    * chromosome = var.CHROM
    * position = var.POS
    * reference allele = var.REF
    * alternative allele = var.ALT
    * [missing] reference aa of the protein [gloria]
    * [missing] alternative aa of the protein [gloria]
    * label (TP or TN) (Clinical Significance by CLinVar)= var.INFO.get('CLNSIG','')
4. Additional variables used in FH-EARLY:
    * [uncertain] function = for now var.INFO.get('MC','') (eg. synonymous_variant)
    * gene = var.INFO.get('GENEINFO', '')
    * variant type = var.INFO.get('CLNVC','')
    * [uncertain] change = for now included in var.INFO.get('CLNHGVS','') (look for >)
    * ONIM = included in var.INFO.CLNDISDB (look for ONIM)
5. Additional variables needed to select samples
    * id = var.INFO.get('ALLELEID', '')
    * star review = var.INFO.get('CLNREVSTAT','')
    * rs# = var.INFO.get('RS', '')
6. Additional variables we need to get output from 1000 genomes, gnomAD exome, and dbSNP
    * TODO

In [66]:
vcf_og = VCF('clinvar_20260208.vcf.gz')

In [67]:
rows = []
for var in vcf_og('19:11087732-11133700'):
    # TODO: select necessary information
    rows.append({
        # identifiers
        'allele_id': var.INFO.get('ALLELEID', ''),
        'rs#': var.INFO.get('RS', ''),
        'review': var.INFO.get('CLNREVSTAT',''),
        'gene': var.INFO.get('GENEINFO', ''),
        'chrom': var.CHROM,
        # useful
        'pos': var.POS,  # 1-based
        # 'ref': var.REF, fetch it from other file
        # 'alt': ','.join(var.ALT), fetch it from other file
        # missing: 'ref_aa': fetch it from other file
        # missing: 'alt_aa': fetch it from other file
        'clinsig': var.INFO.get('CLNSIG', ''),
        'function': var.INFO.get('MC',''),
        'type': var.INFO.get('CLNVC',''),
        'change': var.INFO.get('CLNHGVS',''),
        'onim': var.INFO.get('CLNDISDB','')
    })

vcf_df = pd.DataFrame(rows)
vcf_df

[W::hts_idx_load3] The index file is older than the data file: clinvar_20260208.vcf.gz.tbi


allele_id         rs#  \
0        682121               
1        424286   989307060   
2        245300    17249134   
3       4180223               
4       3752756               
5       2967261  2515905935   
6        424287  1555800611   
7        425023   376713337   
8        514374  1555800612   
9        245301   879254359   
10      4009749               
11      3233868  2515905969   
12       914649    17249141   
13       245302    17249141   
14      3546099               
15      2133128   879254360   
16       245303   879254360   
17      3234085   879254360   
18      3546100               
19       245304   879254361   
20      1953301  2515906014   
21       228112   549995837   
22       914650  1310257411   
23      3234793  2515906029   
24      3234644  2515906048   
25      3843328               
26       914651  2077054310   
27       431951  1270618112   
28      3231029  2515906062   
29       434181  1555800620   
30       245305   879254362   
31       914652   934415028   
32      3848571               
33       979958  2077054428   
34       243265   878854023   
35      1447760  2077054466   
36       245307   879254363   
37      3230603  2515906109   
38      4180224               
39      1882660  2515906117   
40      3234742  2515906125   
41       434182  1555800629   
42       914653  1230170597   
43       362661  1057519647   
44      1876113  1238262444   
45       914654  1238262444   
46      1161494   934014113   
47      2162730  2515906190   
48       245308   879254364   
49       362662  1057519648   
50       245309   879254365   
51       245310   879254366   
52       245311   879254367   
53      2973851  1555800631   
54       434183  1555800631   
55       434184  1555800632   
56       245312   879254368   
57      3546101               
58       245313   879254369   
59       424288   879254370   
60       245314   879254370   
61      4180209               
62       914655  2077055015   
63       390608   875989887   
64       245315   875989887   
65       228113   875989887   
66       245316   879254371   
67       245317   879254371   
68      1322614   879254371   
69        18784   387906307   
70       245318   879254372   
71       245319   879254373   
72      1450687   879254374   
73       245320   879254374   
74       245321   879254374   
75       514375   879254375   
76       245322   879254375   
77       914656  2077055227   
78      3546102               
79      3233842  2515906348   
80       362663  1057519649   
81      3231802  1322549744   
82       618928  1568582299   
83       914657  1568582299   
84       228114   777716188   
85       914658   875989886   
86       228115   875989886   
87      3229475  2515906397   
88      3231500  2515906409   
89      1152820  2147186108   
90       914659  1164871419   
91       618929  1568582310   
92      3231569  2515906450   
93       914660  1357531646   
94       245323   747068848   
95       362664  1057519650   
96       434185  1555800648   
97       424289   944580031   
98       914661   944580031   
99       879825   944580031   
100     3232217  1212116636   
101      914662  1212116636   
102     2934220  2515906549   
103      245324   879254376   
104     3546103               
105     1866569  1247322702   
106     3788824               
107     2934221  2515906622   
108     3546104               
109     3546105               
110     4548538               
111      245325   879254377   
112     3228592  1038988825   
113     2870178  2515906699   
114      914663  2077055920   
115     2934222   371800370   
116     3546106               
117     3233630   769235371   
118     1161495  2147186240   
119     4009925               
120     3230415   879254378   
121      245326   879254378   
122     4009566               
123      424290  1131692188   
124     1323208   930509187   
125     3230652   750462653   
126      245327   763282380   
127      914664   763282380   
128    

* id is unique
* pos is almost unique, there are some variants in the same position
* missing aa info

# Get AA change info from variant_summary
* Source: https://ftp.ncbi.nlm.nih.gov/pub/clinvar/tab_delimited/variant_summary.txt.gz
* Goal: get name field, extract ref, pos, aa_ref, aa_pos
* Link df to samples available in vcf: use AlleleID to link; select Assembly=='GRCh38'

In [68]:
summary_og = pd.read_csv('variant_summary.txt.gz', sep='\t')

/tmp/ipykernel_483683/2743894289.py:1: DtypeWarning: Columns (0: Chromosome) have mixed types. Specify dtype option on import or set low_memory=False.
  summary_og = pd.read_csv('variant_summary.txt.gz', sep='\t')


In [69]:
summary_df = summary_og.loc[summary_og['GeneID']==3949] # Filter for LDLR gene
summary_df = summary_df.loc[summary_df['Assembly']=='GRCh38'] # Filter for h38 assembly
print("Shape: ", summary_df.shape)
summary_df.head()

Shape:  (4402, 43)


#AlleleID                       Type  \
6764      18722  single nucleotide variant   
6766      18724  single nucleotide variant   
6768      18725  single nucleotide variant   
6770      18727  single nucleotide variant   
6772      18728  single nucleotide variant   

                                           Name  GeneID GeneSymbol    HGNC_ID  \
6764     NM_000527.5(LDLR):c.97C>T (p.Gln33Ter)    3949       LDLR  HGNC:6547   
6766    NM_000527.5(LDLR):c.259T>G (p.Trp87Gly)    3949       LDLR  HGNC:6547   
6768   NM_000527.5(LDLR):c.530C>T (p.Ser177Leu)    3949       LDLR  HGNC:6547   
6770  NM_000527.5(LDLR):c.1694G>T (p.Gly565Val)    3949       LDLR  HGNC:6547   
6772  NM_000527.5(LDLR):c.2000G>A (p.Cys667Tyr)    3949       LDLR  HGNC:6547   

              ClinicalSignificance  ClinSigSimple LastEvaluated  RS# (dbSNP)  \
6764                    Pathogenic              1  Mar 25, 2022    121908024   
6766                    Pathogenic              1  Jun 07, 2021    121908025   
6768                    Pathogenic              1  Jun 03, 2022    121908026   
6770  Pathogenic/Likely pathogenic              1  Jul 08, 2024     28942082   
6772             Likely pathogenic              1  Jun 18, 2021     28942083   

     nsv/esv (dbVar)                                       RCVaccession  \
6764               -  RCV000003868|RCV000786350|RCV001034691|RCV0023...   
6766               -  RCV000003870|RCV000622852|RCV000776466|RCV0008...   
6768               -  RCV000003871|RCV000161958|RCV000588687|RCV0023...   
6770               -  RCV000003874|RCV000791454|RCV001195593|RCV0023...   
6772               -  RCV000030131|RCV000313287|RCV000775084|RCV0024...   

                                           PhenotypeIDS  \
6764  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6766  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6768  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6770  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6772  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   

                                          PhenotypeList  \
6764  Hypercholesterolemia, familial, 1|not provided...   
6766  Hypercholesterolemia, familial, 1|not provided...   
6768  Hypercholesterolemia, familial, 1|not provided...   
6770  Hypercholesterolemia, familial, 1|Familial hyp...   
6772  Hypercholesterolemia, familial, 1|not provided...   

                                         Origin OriginSimple Assembly  \
6764                           germline;unknown     germline   GRCh38   
6766                 germline;inherited;unknown     germline   GRCh38   
6768  germline;inherited;not applicable;unknown     germline   GRCh38   
6770                    germline;not applicable     germline   GRCh38   
6772                           germline;unknown     germline   GRCh38   

     ChromosomeAccession Chromosome     Start      Stop ReferenceAllele  \
6764        NC_000019.10         19  11100252  11100252              na   
6766        NC_000019.10         19  11102732  11102732              na   
6768        NC_000019.10         19  11105436  11105436              na   
6770        NC_000019.10         19  11116201  11116201              na   
6772        NC_000019.10         19  11120382  11120382              na   

     AlternateAllele Cytogenetic  \
6764              na     19p13.2   
6766              na     19p13.2   
6768              na     19p13.2   
6770              na     19p13.2   
6772              na     19p13.2   

                                           ReviewStatus  NumberSubmitters  \
6764                           reviewed by expert panel                20   
6766                           reviewed by expert panel                30   
6768                           reviewed by expert panel                28   
6770  criteria provided, multiple submitters, no con...                12   
6772                           reviewed by expert panel                21   

                              

In [70]:
# Link variant_summary df to vcf_file df
filtered_df = summary_df.loc[summary_df['#AlleleID'].isin(vcf_df['allele_id'])]
print("Shape: ", filtered_df.shape)
filtered_df.head()

Shape:  (4321, 43)


#AlleleID                       Type  \
6764      18722  single nucleotide variant   
6766      18724  single nucleotide variant   
6768      18725  single nucleotide variant   
6770      18727  single nucleotide variant   
6772      18728  single nucleotide variant   

                                           Name  GeneID GeneSymbol    HGNC_ID  \
6764     NM_000527.5(LDLR):c.97C>T (p.Gln33Ter)    3949       LDLR  HGNC:6547   
6766    NM_000527.5(LDLR):c.259T>G (p.Trp87Gly)    3949       LDLR  HGNC:6547   
6768   NM_000527.5(LDLR):c.530C>T (p.Ser177Leu)    3949       LDLR  HGNC:6547   
6770  NM_000527.5(LDLR):c.1694G>T (p.Gly565Val)    3949       LDLR  HGNC:6547   
6772  NM_000527.5(LDLR):c.2000G>A (p.Cys667Tyr)    3949       LDLR  HGNC:6547   

              ClinicalSignificance  ClinSigSimple LastEvaluated  RS# (dbSNP)  \
6764                    Pathogenic              1  Mar 25, 2022    121908024   
6766                    Pathogenic              1  Jun 07, 2021    121908025   
6768                    Pathogenic              1  Jun 03, 2022    121908026   
6770  Pathogenic/Likely pathogenic              1  Jul 08, 2024     28942082   
6772             Likely pathogenic              1  Jun 18, 2021     28942083   

     nsv/esv (dbVar)                                       RCVaccession  \
6764               -  RCV000003868|RCV000786350|RCV001034691|RCV0023...   
6766               -  RCV000003870|RCV000622852|RCV000776466|RCV0008...   
6768               -  RCV000003871|RCV000161958|RCV000588687|RCV0023...   
6770               -  RCV000003874|RCV000791454|RCV001195593|RCV0023...   
6772               -  RCV000030131|RCV000313287|RCV000775084|RCV0024...   

                                           PhenotypeIDS  \
6764  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6766  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6768  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6770  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   
6772  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   

                                          PhenotypeList  \
6764  Hypercholesterolemia, familial, 1|not provided...   
6766  Hypercholesterolemia, familial, 1|not provided...   
6768  Hypercholesterolemia, familial, 1|not provided...   
6770  Hypercholesterolemia, familial, 1|Familial hyp...   
6772  Hypercholesterolemia, familial, 1|not provided...   

                                         Origin OriginSimple Assembly  \
6764                           germline;unknown     germline   GRCh38   
6766                 germline;inherited;unknown     germline   GRCh38   
6768  germline;inherited;not applicable;unknown     germline   GRCh38   
6770                    germline;not applicable     germline   GRCh38   
6772                           germline;unknown     germline   GRCh38   

     ChromosomeAccession Chromosome     Start      Stop ReferenceAllele  \
6764        NC_000019.10         19  11100252  11100252              na   
6766        NC_000019.10         19  11102732  11102732              na   
6768        NC_000019.10         19  11105436  11105436              na   
6770        NC_000019.10         19  11116201  11116201              na   
6772        NC_000019.10         19  11120382  11120382              na   

     AlternateAllele Cytogenetic  \
6764              na     19p13.2   
6766              na     19p13.2   
6768              na     19p13.2   
6770              na     19p13.2   
6772              na     19p13.2   

                                           ReviewStatus  NumberSubmitters  \
6764                           reviewed by expert panel                20   
6766                           reviewed by expert panel                30   
6768                           reviewed by expert panel                28   
6770  criteria provided, multiple submitters, no con...                12   
6772                           reviewed by expert panel                21   

                              

In [71]:
filtered_df.loc[filtered_df['#AlleleID']==18722]

#AlleleID                       Type  \
6764      18722  single nucleotide variant   

                                        Name  GeneID GeneSymbol    HGNC_ID  \
6764  NM_000527.5(LDLR):c.97C>T (p.Gln33Ter)    3949       LDLR  HGNC:6547   

     ClinicalSignificance  ClinSigSimple LastEvaluated  RS# (dbSNP)  \
6764           Pathogenic              1  Mar 25, 2022    121908024   

     nsv/esv (dbVar)                                       RCVaccession  \
6764               -  RCV000003868|RCV000786350|RCV001034691|RCV0023...   

                                           PhenotypeIDS  \
6764  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...   

                                          PhenotypeList            Origin  \
6764  Hypercholesterolemia, familial, 1|not provided...  germline;unknown   

     OriginSimple Assembly ChromosomeAccession Chromosome     Start      Stop  \
6764     germline   GRCh38        NC_000019.10         19  11100252  11100252   

     ReferenceAllele AlternateAllele Cytogenetic              ReviewStatus  \
6764              na              na     19p13.2  reviewed by expert panel   

      NumberSubmitters                           Guidelines TestedInGTR  \
6764                20  ACMG2013,ACMG2016,ACMG2021,ACMG2022           N   

                                               OtherIDs  SubmitterCategories  \
6764  ClinGen:CA023802,LDLR-LOVD, British Heart Foun...                    3   

      VariationID  PositionVCF ReferenceAlleleVCF AlternateAlleleVCF  \
6764         3683     11100252                  C                  T   

     SomaticClinicalImpact SomaticClinicalImpactLastEvaluated  \
6764                     -                                  -   

     ReviewStatusClinicalImpact Oncogenicity OncogenicityLastEvaluated  \
6764                          -            -                         -   

     ReviewStatusOncogenicity SCVsForAggregateGermlineClassification  \
6764                        -                           SCV002506409   

     SCVsForAggregateSomaticClinicalImpact  \
6764                                     -   

     SCVsForAggregateOncogenicityClassification  
6764                                          -

In [72]:
vcf_df.loc[vcf_df['allele_id']==18722]

allele_id        rs#                    review       gene chrom  \
280      18722  121908024  reviewed_by_expert_panel  LDLR:3949    19   

          pos     clinsig             function                       type  \
280  11100252  Pathogenic  SO:0001587|nonsense  single_nucleotide_variant   

                         change  \
280  NC_000019.10:g.11100252C>T   

                                                  onim  
280  MedGen:CN230736|MONDO:MONDO:0005439,MedGen:C00...

In [73]:
cols_to_use = ['#AlleleID', 'RS# (dbSNP)', 'Stop', 'Name', 'ReferenceAlleleVCF', 'AlternateAlleleVCF', 'ClinSigSimple']
filtered_df = filtered_df[cols_to_use]
print("Shape: ", filtered_df.shape)
filtered_df.head()

Shape:  (4321, 7)


#AlleleID  RS# (dbSNP)      Stop  \
6764      18722    121908024  11100252   
6766      18724    121908025  11102732   
6768      18725    121908026  11105436   
6770      18727     28942082  11116201   
6772      18728     28942083  11120382   

                                           Name ReferenceAlleleVCF  \
6764     NM_000527.5(LDLR):c.97C>T (p.Gln33Ter)                  C   
6766    NM_000527.5(LDLR):c.259T>G (p.Trp87Gly)                  T   
6768   NM_000527.5(LDLR):c.530C>T (p.Ser177Leu)                  C   
6770  NM_000527.5(LDLR):c.1694G>T (p.Gly565Val)                  G   
6772  NM_000527.5(LDLR):c.2000G>A (p.Cys667Tyr)                  G   

     AlternateAlleleVCF  ClinSigSimple  
6764                  T              1  
6766                  G              1  
6768                  T              1  
6770                  T              1  
6772                  A              1

# Combine VCF and Variant_Summary dataframes
1. Using Labels from variant_summary - way less unknown samples (1(Pathogenic) vs 0(Benign/Uncertain))
2. Remove duplication (too complicated to encode) samples


In [74]:
vcf_df_filtered = vcf_df.loc[vcf_df['allele_id'].isin(filtered_df['#AlleleID'])]
print(vcf_df_filtered.shape)
vcf_df_filtered.head()

(4321, 11)


allele_id         rs#                                             review  \
1     424286   989307060                           reviewed_by_expert_panel   
2     245300    17249134  criteria_provided,_multiple_submitters,_no_con...   
3    4180223                                 no_assertion_criteria_provided   
4    3752756                            criteria_provided,_single_submitter   
5    2967261  2515905935                criteria_provided,_single_submitter   

                           gene chrom       pos                 clinsig  \
1  LDLR:3949|LDLR-AS1:115271120    19  11089263  Uncertain_significance   
2  LDLR:3949|LDLR-AS1:115271120    19  11089281    Benign/Likely_benign   
3  LDLR:3949|LDLR-AS1:115271120    19  11089283  Uncertain_significance   
4  LDLR:3949|LDLR-AS1:115271120    19  11089309  Uncertain_significance   
5  LDLR:3949|LDLR-AS1:115271120    19  11089318  Uncertain_significance   

                                   function                       type  \
1  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
2  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
3  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
4  SO:0001619|non-coding_transcript_variant             Microsatellite   
5  SO:0001619|non-coding_transcript_variant                   Deletion   

                         change  \
1    NC_000019.10:g.11089263C>G   
2    NC_000019.10:g.11089281G>T   
3    NC_000019.10:g.11089283C>T   
4  NC_000019.10:g.11089310AG[1]   
5    NC_000019.10:g.11089319del   

                                                onim  
1  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...  
2  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...  
3  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890  
4  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890  
5  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890

In [75]:
merged_df = vcf_df_filtered.merge(
    filtered_df,
    left_on='allele_id',
    right_on='#AlleleID',
    how='left'
)
print(merged_df.shape)
merged_df.head()

(4321, 18)


allele_id         rs#                                             review  \
0     424286   989307060                           reviewed_by_expert_panel   
1     245300    17249134  criteria_provided,_multiple_submitters,_no_con...   
2    4180223                                 no_assertion_criteria_provided   
3    3752756                            criteria_provided,_single_submitter   
4    2967261  2515905935                criteria_provided,_single_submitter   

                           gene chrom       pos                 clinsig  \
0  LDLR:3949|LDLR-AS1:115271120    19  11089263  Uncertain_significance   
1  LDLR:3949|LDLR-AS1:115271120    19  11089281    Benign/Likely_benign   
2  LDLR:3949|LDLR-AS1:115271120    19  11089283  Uncertain_significance   
3  LDLR:3949|LDLR-AS1:115271120    19  11089309  Uncertain_significance   
4  LDLR:3949|LDLR-AS1:115271120    19  11089318  Uncertain_significance   

                                   function                       type  \
0  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
1  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
2  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
3  SO:0001619|non-coding_transcript_variant             Microsatellite   
4  SO:0001619|non-coding_transcript_variant                   Deletion   

                         change  \
0    NC_000019.10:g.11089263C>G   
1    NC_000019.10:g.11089281G>T   
2    NC_000019.10:g.11089283C>T   
3  NC_000019.10:g.11089310AG[1]   
4    NC_000019.10:g.11089319del   

                                                onim  #AlleleID  RS# (dbSNP)  \
0  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     424286    989307060   
1  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     245300     17249134   
2  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    4180223           -1   
3  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    3752756           -1   
4  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    2967261   2515905935   

       Stop                          Name ReferenceAlleleVCF  \
0  11089263   NM_000527.5(LDLR):c.-286C>G                  C   
1  11089281   NM_000527.5(LDLR):c.-268G>T                  G   
2  11089283   NM_000527.4(LDLR):c.-266C>T                  C   
3  11089311  NC_000019.10:g.11089310AG[1]                CAG   
4  11089319    NC_000019.10:g.11089319del                 AC   

  AlternateAlleleVCF  ClinSigSimple  
0                  G              1  
1                  T              0  
2                  T              0  
3                  C              0  
4                  A              0

In [76]:
# rename useful columns
merged_df = merged_df.rename(columns={
    'chrom': 'chr',
    'Stop': 'end',
    'ReferenceAlleleVCF': 'ref',
    'AlternateAlleleVCF': 'alt',
    'onim': 'ONIM'
})

In [77]:
# filter on submissions
merged_df['review'].value_counts()

review
criteria_provided,_single_submitter                     1872
criteria_provided,_multiple_submitters,_no_conflicts    1432
reviewed_by_expert_panel                                 534
criteria_provided,_conflicting_classifications           292
no_assertion_criteria_provided                           155
                                                          25
no_classification_provided                                 7
no_classification_for_the_single_variant                   4
Name: count, dtype: int64

In [78]:
# define criteria to keep sample (at least one star in https://www-ncbi-nlm-nih-gov.tudelft.idm.oclc.org/clinvar/docs/review_status/)
to_keep = ['criteria_provided,_single_submitter', 'criteria_provided,_multiple_submitters,_no_conflicts', 'reviewed_by_expert_panel']
merged_df = merged_df.loc[merged_df['review'].isin(to_keep)]
print(merged_df.shape)
merged_df.head()

(3838, 18)


allele_id         rs#                                             review  \
0     424286   989307060                           reviewed_by_expert_panel   
1     245300    17249134  criteria_provided,_multiple_submitters,_no_con...   
3    3752756                            criteria_provided,_single_submitter   
4    2967261  2515905935                criteria_provided,_single_submitter   
5     424287  1555800611                criteria_provided,_single_submitter   

                           gene chr       pos                 clinsig  \
0  LDLR:3949|LDLR-AS1:115271120  19  11089263  Uncertain_significance   
1  LDLR:3949|LDLR-AS1:115271120  19  11089281    Benign/Likely_benign   
3  LDLR:3949|LDLR-AS1:115271120  19  11089309  Uncertain_significance   
4  LDLR:3949|LDLR-AS1:115271120  19  11089318  Uncertain_significance   
5  LDLR:3949|LDLR-AS1:115271120  19  11089318              Pathogenic   

                                   function                       type  \
0  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
1  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
3  SO:0001619|non-coding_transcript_variant             Microsatellite   
4  SO:0001619|non-coding_transcript_variant                   Deletion   
5  SO:0001619|non-coding_transcript_variant                   Deletion   

                                change  \
0           NC_000019.10:g.11089263C>G   
1           NC_000019.10:g.11089281G>T   
3         NC_000019.10:g.11089310AG[1]   
4           NC_000019.10:g.11089319del   
5  NC_000019.10:g.11089320_11089459del   

                                                ONIM  #AlleleID  RS# (dbSNP)  \
0  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     424286    989307060   
1  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     245300     17249134   
3  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    3752756           -1   
4  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    2967261   2515905935   
5  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...     424287   1555800611   

        end                             Name  \
0  11089263      NM_000527.5(LDLR):c.-286C>G   
1  11089281      NM_000527.5(LDLR):c.-268G>T   
3  11089311     NC_000019.10:g.11089310AG[1]   
4  11089319       NC_000019.10:g.11089319del   
5  11089458  NM_000527.4(LDLR):c.-229_-90del   

                                                 ref alt  ClinSigSimple  
0                                                  C   G              1  
1                                                  G   T              0  
3                                                CAG   C              0  
4                                                 AC   A              0  
5  ACGGGTTAAAAAGCCGATGTCACATCGGCCGTTCGAAACTCCTCCT...   A              1

In [79]:
# filter on known labels
merged_df = merged_df.loc[~(merged_df['ClinSigSimple']==-1)]
print(merged_df.shape)
merged_df.head()

(3838, 18)


allele_id         rs#                                             review  \
0     424286   989307060                           reviewed_by_expert_panel   
1     245300    17249134  criteria_provided,_multiple_submitters,_no_con...   
3    3752756                            criteria_provided,_single_submitter   
4    2967261  2515905935                criteria_provided,_single_submitter   
5     424287  1555800611                criteria_provided,_single_submitter   

                           gene chr       pos                 clinsig  \
0  LDLR:3949|LDLR-AS1:115271120  19  11089263  Uncertain_significance   
1  LDLR:3949|LDLR-AS1:115271120  19  11089281    Benign/Likely_benign   
3  LDLR:3949|LDLR-AS1:115271120  19  11089309  Uncertain_significance   
4  LDLR:3949|LDLR-AS1:115271120  19  11089318  Uncertain_significance   
5  LDLR:3949|LDLR-AS1:115271120  19  11089318              Pathogenic   

                                   function                       type  \
0  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
1  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
3  SO:0001619|non-coding_transcript_variant             Microsatellite   
4  SO:0001619|non-coding_transcript_variant                   Deletion   
5  SO:0001619|non-coding_transcript_variant                   Deletion   

                                change  \
0           NC_000019.10:g.11089263C>G   
1           NC_000019.10:g.11089281G>T   
3         NC_000019.10:g.11089310AG[1]   
4           NC_000019.10:g.11089319del   
5  NC_000019.10:g.11089320_11089459del   

                                                ONIM  #AlleleID  RS# (dbSNP)  \
0  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     424286    989307060   
1  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     245300     17249134   
3  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    3752756           -1   
4  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    2967261   2515905935   
5  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...     424287   1555800611   

        end                             Name  \
0  11089263      NM_000527.5(LDLR):c.-286C>G   
1  11089281      NM_000527.5(LDLR):c.-268G>T   
3  11089311     NC_000019.10:g.11089310AG[1]   
4  11089319       NC_000019.10:g.11089319del   
5  11089458  NM_000527.4(LDLR):c.-229_-90del   

                                                 ref alt  ClinSigSimple  
0                                                  C   G              1  
1                                                  G   T              0  
3                                                CAG   C              0  
4                                                 AC   A              0  
5  ACGGGTTAAAAAGCCGATGTCACATCGGCCGTTCGAAACTCCTCCT...   A              1

In [80]:
# get p. info
merged_df['protein_info'] = (
    merged_df['Name'].astype(str)
    .str.extract(r'p\.(.+)', expand=False)
    .str.rstrip(')')
)
merged_df[['aa_ref', 'aa_change', 'aa_alt']] = (
    merged_df['protein_info'].str.extract(r'([A-Z][a-z]{2})(\d+)(.*)')
)
merged_df.loc[~merged_df['protein_info'].isna()].head()

allele_id         rs#                               review  \
139    1866537  2515907041  criteria_provided,_single_submitter   
140     245332   879254382             reviewed_by_expert_panel   
141     245333   879254382             reviewed_by_expert_panel   
142     245334   879254382             reviewed_by_expert_panel   
143     434816  1555800701             reviewed_by_expert_panel   

                             gene chr       pos            clinsig  \
139  LDLR:3949|LDLR-AS1:115271120  19  11089548         Pathogenic   
140  LDLR:3949|LDLR-AS1:115271120  19  11089549         Pathogenic   
141  LDLR:3949|LDLR-AS1:115271120  19  11089549  Likely_pathogenic   
142  LDLR:3949|LDLR-AS1:115271120  19  11089549         Pathogenic   
143  LDLR:3949|LDLR-AS1:115271120  19  11089550  Likely_pathogenic   

                                              function  \
139  SO:0001582|initiator_codon_variant,SO:0001589|...   
140  SO:0001582|initiator_codon_variant,SO:0001583|...   
141  SO:0001582|initiator_codon_variant,SO:0001583|...   
142  SO:0001582|initiator_codon_variant,SO:0001583|...   
143  SO:0001582|initiator_codon_variant,SO:0001583|...   

                          type                               change  \
139                   Deletion  NC_000019.10:g.11089549_11089615del   
140  single_nucleotide_variant           NC_000019.10:g.11089549A>C   
141  single_nucleotide_variant           NC_000019.10:g.11089549A>G   
142  single_nucleotide_variant           NC_000019.10:g.11089549A>T   
143  single_nucleotide_variant           NC_000019.10:g.11089550T>C   

                                                  ONIM  #AlleleID  \
139                                    MedGen:C3661900    1866537   
140  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...     245332   
141  MedGen:CN230736|MONDO:MONDO:0005439,MedGen:C00...     245333   
142  MedGen:CN230736|MONDO:MONDO:0005439,MedGen:C00...     245334   
143  MedGen:C4229399|MONDO:MONDO:0007750,MedGen:C07...     434816   

     RS# (dbSNP)       end                                    Name  \
139   2515907041  11089615  NM_000527.5(LDLR):c.1_67del (p.Met1fs)   
140    879254382  11089549    NM_000527.5(LDLR):c.1A>C (p.Met1Leu)   
141    879254382  11089549    NM_000527.5(LDLR):c.1A>G (p.Met1Val)   
142    879254382  11089549    NM_000527.5(LDLR):c.1A>T (p.Met1Leu)   
143   1555800701  11089550    NM_000527.5(LDLR):c.2T>C (p.Met1Thr)   

                                                   ref alt  ClinSigSimple  \
139  CATGGGGCCCTGGGGCTGGAAATTGCGCTGGACCGTCGCCTTGCTC...   C              1   
140                                                  A   C              1   
141                                                  A   G              1   
142                                                  A   T              1   
143                                                  T   C              1   

    protein_info aa_ref aa_change aa_alt  
139       Met1fs    Met         1     fs  
140      Met1Leu    Met         1    Leu  
141      Met1Val    Met         1    Val  
142      Met1Leu    Met         1    Leu  
143      Met1Thr    Met         1    Thr

In [81]:
pd.set_option('display.max_rows', None)
merged_df['aa_alt'].value_counts()

aa_alt
fs                                                                                                                                             560
=                                                                                                                                              547
Ter                                                                                                                                            206
Ser                                                                                                                                            155
Arg                                                                                                                                            153
Gly                                                                                                                                            116
Tyr                                                                                                            

### aa changes to remove (focusing on aa_alt)
Basically every change that involves more than one aa

In [82]:
to_drop = merged_df['aa_alt'].value_counts()[merged_df['aa_alt'].value_counts() == 1].index.tolist()
to_drop = to_drop + ['_Asp227dup', '_Ser213del', '_Asp227del', '_Cys231del']
print("Values to remove: ", len(to_drop))

Values to remove:  127


In [83]:
# remove samples that have more that one aa change
merged_df = merged_df.loc[~merged_df['aa_alt'].isin(to_drop)]
print(merged_df.shape)
merged_df.head()

(3706, 22)


allele_id         rs#                                             review  \
0     424286   989307060                           reviewed_by_expert_panel   
1     245300    17249134  criteria_provided,_multiple_submitters,_no_con...   
3    3752756                            criteria_provided,_single_submitter   
4    2967261  2515905935                criteria_provided,_single_submitter   
5     424287  1555800611                criteria_provided,_single_submitter   

                           gene chr       pos                 clinsig  \
0  LDLR:3949|LDLR-AS1:115271120  19  11089263  Uncertain_significance   
1  LDLR:3949|LDLR-AS1:115271120  19  11089281    Benign/Likely_benign   
3  LDLR:3949|LDLR-AS1:115271120  19  11089309  Uncertain_significance   
4  LDLR:3949|LDLR-AS1:115271120  19  11089318  Uncertain_significance   
5  LDLR:3949|LDLR-AS1:115271120  19  11089318              Pathogenic   

                                   function                       type  \
0  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
1  SO:0001619|non-coding_transcript_variant  single_nucleotide_variant   
3  SO:0001619|non-coding_transcript_variant             Microsatellite   
4  SO:0001619|non-coding_transcript_variant                   Deletion   
5  SO:0001619|non-coding_transcript_variant                   Deletion   

                                change  \
0           NC_000019.10:g.11089263C>G   
1           NC_000019.10:g.11089281G>T   
3         NC_000019.10:g.11089310AG[1]   
4           NC_000019.10:g.11089319del   
5  NC_000019.10:g.11089320_11089459del   

                                                ONIM  #AlleleID  RS# (dbSNP)  \
0  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     424286    989307060   
1  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...     245300     17249134   
3  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    3752756           -1   
4  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890    2967261   2515905935   
5  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...     424287   1555800611   

        end                             Name  \
0  11089263      NM_000527.5(LDLR):c.-286C>G   
1  11089281      NM_000527.5(LDLR):c.-268G>T   
3  11089311     NC_000019.10:g.11089310AG[1]   
4  11089319       NC_000019.10:g.11089319del   
5  11089458  NM_000527.4(LDLR):c.-229_-90del   

                                                 ref alt  ClinSigSimple  \
0                                                  C   G              1   
1                                                  G   T              0   
3                                                CAG   C              0   
4                                                 AC   A              0   
5  ACGGGTTAAAAAGCCGATGTCACATCGGCCGTTCGAAACTCCTCCT...   A              1   

  protein_info aa_ref aa_change aa_alt  
0          NaN    NaN       NaN    NaN  
1          NaN    NaN       NaN    NaN  
3          NaN    NaN       NaN    NaN  
4          NaN    NaN       NaN    NaN  
5          NaN    NaN       NaN    NaN

In [84]:
# TODO: Gene LDLR encoding only; ONIM only

In [85]:
useless_cols = ['review', 'clinsig', '#AlleleID', 'RS# (dbSNP)', 'Name', 'protein_info']
on_hold_cols = ['function', 'change']
annovar_cols = ['chr', 'pos', 'end', 'ref', 'alt', 'aa_ref', 'aa_alt', 'ClinSigSimple']

# Prepare Dataset for ANNOVAR

In [86]:
annovar_df = merged_df[annovar_cols]
annovar_df = annovar_df.rename({'pos': 'start'})
annovar_df = annovar_df.fillna('')
print(annovar_df.shape)
annovar_df.head()

(3706, 8)


chr       pos       end                                                ref  \
0  19  11089263  11089263                                                  C   
1  19  11089281  11089281                                                  G   
3  19  11089309  11089311                                                CAG   
4  19  11089318  11089319                                                 AC   
5  19  11089318  11089458  ACGGGTTAAAAAGCCGATGTCACATCGGCCGTTCGAAACTCCTCCT...   

  alt aa_ref aa_alt  ClinSigSimple  
0   G                            1  
1   T                            0  
3   C                            0  
4   A                            0  
5   A                            1

In [87]:
annovar_df.to_csv("mafalda_files/annovar_file.avinput", sep="\t", header=False, index=False)

In [88]:
full_dataset = merged_df.drop(columns=useless_cols).drop(columns=on_hold_cols)
full_dataset = full_dataset.rename({'pos': 'start'})
# full_dataset = full_dataset.fillna('')
print(full_dataset.shape)
full_dataset.head()

(3706, 14)


allele_id         rs#                          gene chr       pos  \
0     424286   989307060  LDLR:3949|LDLR-AS1:115271120  19  11089263   
1     245300    17249134  LDLR:3949|LDLR-AS1:115271120  19  11089281   
3    3752756              LDLR:3949|LDLR-AS1:115271120  19  11089309   
4    2967261  2515905935  LDLR:3949|LDLR-AS1:115271120  19  11089318   
5     424287  1555800611  LDLR:3949|LDLR-AS1:115271120  19  11089318   

                        type  \
0  single_nucleotide_variant   
1  single_nucleotide_variant   
3             Microsatellite   
4                   Deletion   
5                   Deletion   

                                                ONIM       end  \
0  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...  11089263   
1  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143...  11089281   
3  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890  11089311   
4  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890  11089319   
5  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...  11089458   

                                                 ref alt  ClinSigSimple  \
0                                                  C   G              1   
1                                                  G   T              0   
3                                                CAG   C              0   
4                                                 AC   A              0   
5  ACGGGTTAAAAAGCCGATGTCACATCGGCCGTTCGAAACTCCTCCT...   A              1   

  aa_ref aa_change aa_alt  
0    NaN       NaN    NaN  
1    NaN       NaN    NaN  
3    NaN       NaN    NaN  
4    NaN       NaN    NaN  
5    NaN       NaN    NaN

In [90]:
full_dataset.to_csv("mafalda_files/full_dataset.csv", index=False)

In [95]:
df = pd.read_csv("mafalda_files/full_dataset.csv")
df.shape

(3706, 14)

In [94]:
df.loc[df['pos']==11102786]

allele_id           rs#       gene  chr       pos         type  \
523     245477  8.792545e+08  LDLR:3949   19  11102786  Duplication   
524     998358  2.077234e+09  LDLR:3949   19  11102786  Duplication   
525    3499360           NaN  LDLR:3949   19  11102786        Indel   
526    1504833  2.147218e+09  LDLR:3949   19  11102786     Deletion   

                                                  ONIM       end    ref  alt  \
523  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...  11102787      C   CG   
524  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890  11102787      C  CGT   
525  MONDO:MONDO:0007750,MedGen:C0745103,OMIM:14389...  11102787     CG   TC   
526  MONDO:MONDO:0005439,MedGen:C0020445,OMIM:PS143890  11102790  CGTAA    C   

     ClinSigSimple aa_ref  aa_change aa_alt  
523              1    NaN        NaN    NaN  
524              0    NaN        NaN    NaN  
525              1    NaN        NaN    NaN  
526              0    NaN        NaN    NaN